# Task 1: Automatic classification of tweets that report adverse effects

In [1]:
!pip install -q transformers contractions imbalanced-learn ekphrasis

     |████████████████████████████████| 4.0 MB 5.3 MB/s 
     |████████████████████████████████| 80 kB 6.9 MB/s 
     |████████████████████████████████| 880 kB 37.9 MB/s 
     |████████████████████████████████| 596 kB 32.9 MB/s 
     |████████████████████████████████| 77 kB 5.6 MB/s 
     |████████████████████████████████| 6.6 MB 32.6 MB/s 
     |████████████████████████████████| 106 kB 25.4 MB/s 
     |████████████████████████████████| 287 kB 48.5 MB/s 
     |████████████████████████████████| 45 kB 2.3 MB/s 
     |████████████████████████████████| 53 kB 1.2 MB/s 


## 1. Import all the necessary libraries and data files

In [2]:
import numpy as np
import pandas as pd

import warnings
import torch
import torch.nn as nn
import time

from sklearn.metrics import classification_report
from torch.utils.data import TensorDataset, DataLoader, RandomSampler, SequentialSampler
from transformers import BertModel, BertTokenizerFast
from transformers import RobertaTokenizerFast, RobertaModel
from ekphrasis.classes.preprocessor import TextPreProcessor
from ekphrasis.classes.tokenizer import SocialTokenizer
from ekphrasis.dicts.emoticons import emoticons
from tqdm import tqdm
from sklearn.metrics import f1_score

warnings.filterwarnings("ignore")
pd.options.display.max_colwidth=None

In [3]:
train_filename = "task2_en_training.tsv"
val_filename = "task2_en_validation.tsv"

In [4]:
# Load data
train = pd.read_csv(train_filename, sep="\t")
validation = pd.read_csv(val_filename, sep="\t")

In [5]:
print(f"Shape of training data is {train.shape} and validation data is {validation.shape}")

Shape of training data is (20544, 4) and validation data is (5134, 4)


In [6]:
# Train top 5 rows
train.head().style.set_caption("Task 1: Train dataset")

## 2. Prepare the data - Clean & Prepare for Model

In [7]:
# Drop unwanted columns
train.drop(['tweet_id', 'user_id'], axis=1, inplace=True)
validation.drop(['tweet_id', 'user_id'], axis=1, inplace=True)

In [8]:
# Referred from: https://github.com/cbaziotis/ekphrasis

text_processor = TextPreProcessor(
    # terms that will be normalized
    normalize=['url', 'email', 'percent', 'money', 'phone', 'user',
        'time', 'url', 'date', 'number'],
    
    # terms that will be annotated
    annotate={"hashtag", "allcaps", "elongated", "repeated",
        'emphasis', 'censored'},
    fix_html=True,  # fix HTML tokens
    
    # corpus from which the word statistics are going to be used 
    # for word segmentation 
    segmenter="twitter", 
    
    # corpus from which the word statistics are going to be used 
    # for spell correction
    corrector="twitter", 
    
    unpack_hashtags=True,  # perform word segmentation on hashtags
    unpack_contractions=True,  # Unpack contractions (can't -> can not)
    spell_correct_elong=False,  # spell correction for elongated words
    
    # select a tokenizer. You can use SocialTokenizer, or pass your own
    # the tokenizer, should take as input a string and return a list of tokens
    tokenizer=SocialTokenizer(lowercase=True).tokenize,
    
    # list of dictionaries, for replacing tokens extracted from the text,
    # with other expressions. You can pass more than one dictionaries.
    dicts=[emoticons]
)

Word statistics files not found!
Downloading... done!
Unpacking... done!
Reading twitter - 1grams ...
generating cache file for faster loading...
reading ngrams /root/.ekphrasis/stats/twitter/counts_1grams.txt
Reading twitter - 2grams ...
generating cache file for faster loading...
reading ngrams /root/.ekphrasis/stats/twitter/counts_2grams.txt
Reading twitter - 1grams ...


In [9]:
train['clean_tweets'] = [" ".join(text_processor.pre_process_doc(tweet)) for tweet in train.tweet]
validation['clean_tweets'] = [" ".join(text_processor.pre_process_doc(tweet)) for tweet in validation.tweet]

In [10]:
# Train top 5 rows after pre-processing
train[['class', 'clean_tweets']].head()

class  \
0      0   
1      0   
2      0   
3      0   
4      0   

                                                                                                                                          clean_tweets  
0                                                                                                                 depression hurts , cymbalta can help  
1    <user> right , but cipro can make things much worse . <repeated> and why give bayer more of your money ? they already screwed you once w / essure  
2                                                                                                     <user> are you on paxil . <repeated> i need help  
3                                                                          <user> the lamotrigine and sjs just made chaos more vengeful and sadistic .  
4  have decided to skip my <hashtag> humira </hashtag> shot today . my body ' s having hysterics , need time to simmer down <hashtag> rheum </hashtag>

In [11]:
BATCH_SIZE = 32
N_EPOCHS = 5

In [12]:
# Define BERT tokenizer
tokenizer = RobertaTokenizerFast.from_pretrained("roberta-base")

Downloading:   0%|          | 0.00/878k [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/446k [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/1.29M [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/481 [00:00<?, ?B/s]

In [13]:
# Tokenize train and validation data
train_enc_rob = tokenizer.batch_encode_plus(train.clean_tweets.to_list(), padding="longest", truncation=True, max_length=128, return_tensors="pt")
valid_enc_rob = tokenizer.batch_encode_plus(validation.clean_tweets.to_list(), padding="longest", truncation=True, max_length=128, return_tensors="pt")

In [14]:
train_enc_rob.keys()

dict_keys(['input_ids', 'attention_mask'])

In [15]:
train_enc_rob.input_ids.shape, train_enc_rob.attention_mask.shape

(torch.Size([20544, 128]), torch.Size([20544, 128]))

In [16]:
def get_dataloader_rob(encoding, target):
    data = (TensorDataset(encoding.input_ids, encoding.attention_mask, target))
    sampler = RandomSampler(data)
    dataloader = DataLoader(data, sampler=sampler, batch_size=BATCH_SIZE)
    return dataloader

In [17]:
train_dataloader_rob = get_dataloader_rob(train_enc_rob, torch.tensor(train['class'].to_list()))
valid_dataloader_rob = get_dataloader_rob(valid_enc_rob, torch.tensor(validation['class'].to_list()))

In [18]:
# Sanity check that the tensors returned by the dataloader are correct
for batch in train_dataloader_rob:
    input_ids, attn_mask, target = batch
    print(input_ids.shape, attn_mask.shape, target.shape)
    break

torch.Size([32, 128]) torch.Size([32, 128]) torch.Size([32])


## 3. Model Building - Roberta

In [19]:
device = 'cuda' if torch.cuda.is_available() else 'cpu'
device

'cuda'

In [20]:
class ROBERTAclassifier(nn.Module):
    def __init__(self, transformer):
        super(ROBERTAclassifier, self).__init__()
        self.transformer = transformer
        self.linear_layer = nn.Linear(768, 2)
    
    def forward(self, ip_ids, attn_mask):
        op = self.transformer(input_ids=ip_ids,
                              attention_mask=attn_mask)
        return  self.linear_layer(op["pooler_output"])

In [21]:
def count_parameter(model):
    return sum(para.numel() for para in model.parameters() if para.requires_grad)

In [22]:
transformer_rob = RobertaModel.from_pretrained("roberta-base")
model_rob = ROBERTAclassifier(transformer_rob).to(device)
print(f"The model has {count_parameter(model_rob)} trainable parameters.")

Downloading:   0%|          | 0.00/478M [00:00<?, ?B/s]

Some weights of the model checkpoint at roberta-base were not used when initializing RobertaModel: ['lm_head.dense.bias', 'lm_head.dense.weight', 'lm_head.decoder.weight', 'lm_head.layer_norm.weight', 'lm_head.layer_norm.bias', 'lm_head.bias']
- This IS expected if you are initializing RobertaModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing RobertaModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


The model has 124647170 trainable parameters.


In [23]:
# Define optimizer 
criterion_rob = torch.nn.CrossEntropyLoss()
optim_rob = torch.optim.AdamW(model_rob.parameters(), lr = 2e-5)

In [ ]:
def train_model_rob(model, dataloader, clip=1.0):
    model.train()

    epoch_loss = 0
    batch_num = 0
    pred, target = [], []

    for index, batch in tqdm(enumerate(dataloader)):
        batch = tuple(row.to(device) for row in batch)
        input_ids, attn_mask, y = batch

        optim_rob.zero_grad()
        output = model(input_ids, attn_mask)
        loss = criterion_rob(output, y)
        loss.backward()

        nn.utils.clip_grad_norm_(model.parameters(), clip)
        optim_rob.step()

        epoch_loss += loss.item()
        batch_num += 1
        pred.extend(torch.argmax(output, -1).tolist())
        target.extend(y.tolist())
    
    return epoch_loss/batch_num, f1_score(target, pred)

def evaluate_rob(model, dataloader):
    model.eval()

    epoch_loss = 0
    batch_num = 0
    pred, target = list(), list()

    for index, batch in enumerate(dataloader):
        batch = tuple(row.to(device) for row in batch)
        input_ids, attn_mask, y = batch
        
        with torch.no_grad():
            output = model(input_ids, attn_mask)
            loss = criterion_rob(output, y)
            
            epoch_loss += loss.item()
            batch_num += 1
            pred.extend(torch.argmax(output, -1).tolist())
            target.extend(y.tolist())
    
    return epoch_loss/batch_num, f1_score(target, pred), pred, target

In [ ]:
best_valid_loss_rob = float('inf')
total_train_loss_rob, total_valid_loss_rob = list(), list()

In [ ]:
for epoch in tqdm(range(N_EPOCHS)):
    train_loss, train_f1_score = train_model_rob(model_rob, train_dataloader_rob)
    total_train_loss_rob.append(train_loss)

    valid_loss, valid_f1_score, pred, target = evaluate_rob(model_rob, valid_dataloader_rob)
    total_valid_loss_rob.append(valid_loss)

    if valid_loss < best_valid_loss_rob:
        best_valid_loss_rob = valid_loss
        best_pred, best_target = pred, target
        torch.save(model_rob.state_dict(), "model_least_loss_rob.pt")
        print("\nBest Model Saved!!\n")
    
    torch.save(model_rob.state_dict(), "model_checkpoint_rob" + str(epoch) + ".pt")
    print("Checkpoint Model Saved!\n")

    print(f"Epoch: {epoch+1:02}")
    print(f"Train Total Loss: {train_loss:.3f} | Train F1 Score: {train_f1_score:.3f}")
    print(f"Valid Total Loss: {valid_loss:.3f} | Valid F1 Score: {valid_f1_score:.3f}")
    print("-"*20)

  0%|          | 0/5 [00:00<?, ?it/s]
0it [00:00, ?it/s]
1it [00:00,  1.28it/s]
2it [00:01,  1.43it/s]
3it [00:02,  1.47it/s]
4it [00:02,  1.50it/s]
5it [00:03,  1.52it/s]
6it [00:04,  1.53it/s]
7it [00:04,  1.54it/s]
8it [00:05,  1.55it/s]
9it [00:05,  1.54it/s]
10it [00:06,  1.54it/s]
11it [00:07,  1.54it/s]
12it [00:07,  1.54it/s]
13it [00:08,  1.54it/s]
14it [00:09,  1.53it/s]
15it [00:09,  1.53it/s]
16it [00:10,  1.53it/s]
17it [00:11,  1.52it/s]
18it [00:11,  1.53it/s]
19it [00:12,  1.52it/s]
20it [00:13,  1.52it/s]
21it [00:13,  1.53it/s]
22it [00:14,  1.52it/s]
23it [00:15,  1.52it/s]
24it [00:15,  1.52it/s]
25it [00:16,  1.52it/s]
26it [00:17,  1.51it/s]
27it [00:17,  1.51it/s]
28it [00:18,  1.51it/s]
29it [00:19,  1.52it/s]
30it [00:19,  1.51it/s]
31it [00:20,  1.50it/s]
32it [00:21,  1.50it/s]
33it [00:21,  1.50it/s]
34it [00:22,  1.50it/s]
35it [00:23,  1.49it/s]
36it [00:23,  1.50it/s]
37it [00:24,  1.50it/s]
38it [00:25,  1.49it/s]
39it [00:25,  1.49it/s]
40it [00:26,  1.


Best Model Saved!!



 20%|██        | 1/5 [07:45<31:00, 465.07s/it]

Checkpoint Model Saved!

Epoch: 01
Train Total Loss: 0.216 | Train F1 Score: 0.452
Valid Total Loss: 0.251 | Valid F1 Score: 0.571
--------------------



0it [00:00, ?it/s]
1it [00:00,  1.40it/s]
2it [00:01,  1.48it/s]
3it [00:02,  1.50it/s]
4it [00:02,  1.50it/s]
5it [00:03,  1.51it/s]
6it [00:03,  1.52it/s]
7it [00:04,  1.51it/s]
8it [00:05,  1.51it/s]
9it [00:05,  1.51it/s]
10it [00:06,  1.51it/s]
11it [00:07,  1.52it/s]
12it [00:07,  1.52it/s]
13it [00:08,  1.52it/s]
14it [00:09,  1.51it/s]
15it [00:09,  1.52it/s]
16it [00:10,  1.52it/s]
17it [00:11,  1.51it/s]
18it [00:11,  1.51it/s]
19it [00:12,  1.51it/s]
20it [00:13,  1.51it/s]
21it [00:13,  1.51it/s]
22it [00:14,  1.52it/s]
23it [00:15,  1.51it/s]
24it [00:15,  1.51it/s]
25it [00:16,  1.50it/s]
26it [00:17,  1.51it/s]
27it [00:17,  1.50it/s]
28it [00:18,  1.51it/s]
29it [00:19,  1.50it/s]
30it [00:19,  1.50it/s]
31it [00:20,  1.50it/s]
32it [00:21,  1.51it/s]
33it [00:21,  1.50it/s]
34it [00:22,  1.50it/s]
35it [00:23,  1.50it/s]
36it [00:23,  1.50it/s]
37it [00:24,  1.50it/s]
38it [00:25,  1.50it/s]
39it [00:25,  1.50it/s]
40it [00:26,  1.50it/s]
41it [00:27,  1.49it/s]
42it 

...

Checkpoint Model Saved!

Epoch: 03
Train Total Loss: 0.104 | Train F1 Score: 0.791
Valid Total Loss: 0.229 | Valid F1 Score: 0.604
--------------------



0it [00:00, ?it/s]
1it [00:00,  1.56it/s]
2it [00:01,  1.52it/s]
3it [00:01,  1.52it/s]
4it [00:02,  1.52it/s]
5it [00:03,  1.52it/s]
6it [00:03,  1.52it/s]
7it [00:04,  1.51it/s]
8it [00:05,  1.51it/s]
9it [00:05,  1.52it/s]
10it [00:06,  1.51it/s]
11it [00:07,  1.51it/s]
12it [00:07,  1.51it/s]
13it [00:08,  1.51it/s]
14it [00:09,  1.51it/s]
15it [00:09,  1.51it/s]
16it [00:10,  1.51it/s]
17it [00:11,  1.50it/s]
18it [00:11,  1.50it/s]
19it [00:12,  1.50it/s]
20it [00:13,  1.50it/s]
21it [00:13,  1.50it/s]
22it [00:14,  1.50it/s]
23it [00:15,  1.50it/s]
24it [00:15,  1.50it/s]
25it [00:16,  1.50it/s]
26it [00:17,  1.51it/s]
27it [00:17,  1.51it/s]
28it [00:18,  1.51it/s]
29it [00:19,  1.51it/s]
30it [00:19,  1.51it/s]
31it [00:20,  1.51it/s]
32it [00:21,  1.51it/s]
33it [00:21,  1.50it/s]
34it [00:22,  1.50it/s]
35it [00:23,  1.51it/s]
36it [00:23,  1.51it/s]
37it [00:24,  1.51it/s]
38it [00:25,  1.51it/s]
39it [00:25,  1.51it/s]
40it [00:26,  1.50it/s]
41it [00:27,  1.50it/s]
42it 

Checkpoint Model Saved!

Epoch: 04
Train Total Loss: 0.077 | Train F1 Score: 0.880
Valid Total Loss: 0.244 | Valid F1 Score: 0.632
--------------------



0it [00:00, ?it/s]
1it [00:00,  1.55it/s]
2it [00:01,  1.52it/s]
3it [00:01,  1.52it/s]
4it [00:02,  1.52it/s]
5it [00:03,  1.52it/s]
6it [00:03,  1.52it/s]
7it [00:04,  1.51it/s]
8it [00:05,  1.51it/s]
9it [00:05,  1.51it/s]
10it [00:06,  1.51it/s]
11it [00:07,  1.51it/s]
12it [00:07,  1.51it/s]
13it [00:08,  1.51it/s]
14it [00:09,  1.51it/s]
15it [00:09,  1.51it/s]
16it [00:10,  1.51it/s]
17it [00:11,  1.51it/s]
18it [00:11,  1.50it/s]
19it [00:12,  1.50it/s]
20it [00:13,  1.51it/s]
21it [00:13,  1.51it/s]
22it [00:14,  1.50it/s]
23it [00:15,  1.50it/s]
24it [00:15,  1.50it/s]
25it [00:16,  1.51it/s]
26it [00:17,  1.51it/s]
27it [00:17,  1.51it/s]
28it [00:18,  1.50it/s]
29it [00:19,  1.50it/s]
30it [00:19,  1.50it/s]
31it [00:20,  1.50it/s]
32it [00:21,  1.50it/s]
33it [00:21,  1.50it/s]
34it [00:22,  1.50it/s]
35it [00:23,  1.50it/s]
36it [00:23,  1.49it/s]
37it [00:24,  1.50it/s]
38it [00:25,  1.50it/s]
39it [00:25,  1.50it/s]
40it [00:26,  1.50it/s]
41it [00:27,  1.50it/s]
42it 

Checkpoint Model Saved!

Epoch: 05
Train Total Loss: 0.054 | Train F1 Score: 0.920
Valid Total Loss: 0.376 | Valid F1 Score: 0.591
--------------------


In [ ]:
print(classification_report(best_target, best_pred))

              precision    recall  f1-score   support

           0       0.97      0.95      0.96      4660
           1       0.58      0.70      0.63       474

    accuracy                           0.92      5134
   macro avg       0.77      0.82      0.80      5134
weighted avg       0.93      0.92      0.93      5134



In [ ]:
!zip -r content.zip ../content/ 

  adding: ../content/ (stored 0%)
  adding: ../content/.config/ (stored 0%)
  adding: ../content/.config/.feature_flags_config.yaml (deflated 23%)
  adding: ../content/.config/gce (stored 0%)
  adding: ../content/.config/.last_survey_prompt.yaml (stored 0%)
  adding: ../content/.config/.metricsUUID (stored 0%)
  adding: ../content/.config/.last_opt_in_prompt.yaml (stored 0%)
  adding: ../content/.config/config_sentinel (stored 0%)
  adding: ../content/.config/logs/ (stored 0%)
  adding: ../content/.config/logs/2022.04.19/ (stored 0%)
  adding: ../content/.config/logs/2022.04.19/14.22.58.550404.log (deflated 86%)
  adding: ../content/.config/logs/2022.04.19/14.23.29.232715.log (deflated 54%)
  adding: ../content/.config/logs/2022.04.19/14.23.28.447853.log (deflated 55%)
  adding: ../content/.config/logs/2022.04.19/14.22.14.343189.log (deflated 91%)
  adding: ../content/.config/logs/2022.04.19/14.23.07.556024.log (deflated 54%)
  adding: ../content/.config/logs/2022.04.19/14.22.38.448952

In [ ]:
from google.colab import drive

In [ ]:
drive.mount('/content/gdrive')

Mounted at /content/gdrive


In [ ]:
from glob import glob

In [ ]:
for filepath in glob("*.pt"):
    !cp -r $filepath /content/gdrive/My\ Drive/Colab\ Notebooks/NLP\ Final\ Project/
    time.sleep(10)

In [ ]:
# !cp -r model_least_loss_rob.pt /content/gdrive/My\ Drive/Colab\ Notebooks/NLP\ Final\ Project/

In [ ]:
# with open('/content/gdrive/My Drive/', 'w') as handle:
#     handle.write()

In [24]:
# Loading the saved model
output_model = 'model_least_loss_rob.pt'

model_test = ROBERTAclassifier(transformer_rob).to(device)
model_test.load_state_dict(torch.load(output_model, map_location=device))

<All keys matched successfully>

In [ ]:
# Training set

# Set model to evaluation
# model_test.eval()

# y_pred_train, y_true_train = [], []
# train_indexes_list = []

# for index, batch in enumerate(train_dataloader_rob):
#     batch = tuple(row.to(device) for row in batch)
#     input_ids, attn_mask, target, indexes = batch
    
#     with torch.no_grad():
#         output = model_test(input_ids, attn_mask)
        
#         y_pred_train.extend(torch.argmax(output, -1).tolist())
#         y_true_train.extend(target.tolist())
#         train_indexes_list.extend(indexes.tolist())

In [ ]:
# print(f"F1-score: {f1_score(y_true_train, y_pred_train)}\n", f"Classification report: \n{classification_report(y_true_train, y_pred_train)}", sep='\n')

F1-score: 0.9996512033484479

Classification report: 
              precision    recall  f1-score   support

           0       1.00      1.00      1.00       739
           1       1.00      1.00      1.00      1433

    accuracy                           1.00      2172
   macro avg       1.00      1.00      1.00      2172
weighted avg       1.00      1.00      1.00      2172



In [26]:
# Validation set
model_test.eval()

y_pred_valid, y_true_valid = [], []
valid_indexes_list = []

for index, batch in enumerate(valid_dataloader_rob):
    batch = tuple(row.to(device) for row in batch)
    input_ids, attn_mask, target = batch
    
    with torch.no_grad():
        output = model_test(input_ids, attn_mask)
        
        y_pred_valid.extend(torch.argmax(output, -1).tolist())
        y_true_valid.extend(target.tolist())
        # valid_indexes_list.extend(indexes.tolist())

In [27]:
print(f"F1-score: {f1_score(y_true_valid, y_pred_valid)}\n", f"Classification report: \n{classification_report(y_true_valid, y_pred_valid)}", sep='\n')

F1-score: 0.6323809523809524

Classification report: 
              precision    recall  f1-score   support

           0       0.97      0.95      0.96      4660
           1       0.58      0.70      0.63       474

    accuracy                           0.92      5134
   macro avg       0.77      0.82      0.80      5134
weighted avg       0.93      0.92      0.93      5134



In [29]:
validation['pred'] = y_pred_valid

In [35]:
pd.options.display.max_rows=None

In [36]:
validation[validation['class'] != validation.pred]

class  \
2         0   
5         1   
7         1   
21        1   
22        1   
25        1   
26        1   
34        1   
56        0   
57        0   
70        0   
73        0   
79        0   
83        1   
91        0   
97        1   
98        0   
102       1   
112       0   
115       0   
119       1   
128       0   
135       0   
140       1   
145       0   
146       1   
148       1   
149       0   
153       1   
154       1   
157       1   
158       0   
162       1   
164       0   
171       0   
172       1   
179       1   
192       0   
196       0   
197       1   
199       1   
211       0   
218       0   
221       0   
226       0   
230       1   
233       0   
240       0   
241       1   
249       1   
258       0   
263       1   
273       1   
278       1   
299       1   
301       0   
304       0   
306       1   
308       1   
309       0   
314       0   
321       1   
322       1   
325       0   
327       0   
328       0   
331       0   
336       1   
340       1   
342       0   
343       1   
345       0   
348       0   
349       0   
353       1   
357       0   
360       1   
366       0   
382       0   
393       0   
414       1   
415       0   
416       1   
422       1   
425       0   
431       1   
435       1   
438       0   
448       0   
466       0   
482       0   
484       0   
487       1   
530       0   
532       0   
534       0   
536       0   
537       0   
543       0   
548       0   
563       0   
569       0   
570       0   
580       0   
619       1   
621       0   
631       1   
633       1   
642       1   
645       1   
650       0   
660       0   
669       1   
673       0   
680       1   
682       0   
684       1   
688       0   
690       1   
692       0   
695       0   
698       0   
701       0   
703       0   
714       1   
723       1   
724       1   
728       1   
730       0   
734       1   
735       0   
736       0   
743       0   
746       1   
750       0   
756       1   
758       1   
764       0   
771       0   
775       1   
776       1   
781       0   
783       1   
793       1   
810       1   
815       1   
816       0   
817       1   
823       1   
828       0   
842       0   
845       1   
849       1   
856       0   
858       0   
874       0   
878       1   
883       1   
885       0   
900       0   
902       1   
905       0   
908       0   
910       1   
911       0   
923       0   
935       1   
946       1   
948       0   
951       1   
954       0   
957       1   
966       1   
969       0   
977       0   
983       1   
984       1   
987       1   
992       0   
1005      1   
1006      1   
1007      1   
1013      1   
1014      1   
1015      1   
1022      0   
1027      1   
1031      0   
1035      1   
1040      1   
1051      0   
1056      0   
1063      0   
1071      0   
1075      0   
1084      0   
1085      0   
1090      0   
1098      0   
1099      0   
1120      0   
1130      0   
1138      0   
1147      1   
1151      0   
1157      0   
1159      0   
1160      0   
1165      0   
1171      0   
1178      0   
1181      0   
1185      1   
1188      0   
1224      0   
1250      0   
1269      0   
1289      0   
1290      1   
1291      1   
1293      1   
1295      1   
1298      1   
1299      1   
1313      0   
1320      1   
1321      0   
1326      0   
1331      0   
1347      1   
1354      1   
1358      1   
1362      1   
1364      1   
1367      0   
1370      0   
1371      0   
1384      0   
1385      0   
1393      0   
1405      0   
1409      1   
1410      0   
1411      1   
1413      1   
1416      1   
1418      0   
1422      0   
1424      1   
1427      1   
1431      0   
1448      0   
1457      1   
1458      0   
1463      0   
1465      1   
1471      1   
1474      0   
1476      0   
1479      0   
1486      1   
1491      0   
1492      1   
1493      1   
1494      1   
1501      0   
1

In [37]:
validation[validation['class'] == validation.pred]

class  \
0         0   
1         0   
3         0   
4         0   
6         0   
8         0   
9         0   
10        0   
11        0   
12        0   
13        0   
14        0   
15        0   
16        0   
17        0   
18        0   
19        0   
20        0   
23        0   
24        0   
27        0   
28        0   
29        0   
30        0   
31        0   
32        0   
33        0   
35        0   
36        0   
37        0   
38        0   
39        0   
40        0   
41        0   
42        0   
43        0   
44        0   
45        0   
46        0   
47        0   
48        0   
49        0   
50        0   
51        0   
52        0   
53        0   
54        0   
55        0   
58        0   
59        0   
60        0   
61        0   
62        0   
63        0   
64        1   
65        0   
66        0   
67        0   
68        0   
69        0   
71        0   
72        0   
74        0   
75        0   
76        0   
77        0   
78        0   
80        0   
81        0   
82        0   
84        0   
85        0   
86        0   
87        0   
88        0   
89        0   
90        0   
92        0   
93        0   
94        0   
95        0   
96        0   
99        0   
100       0   
101       0   
103       0   
104       0   
105       0   
106       0   
107       0   
108       0   
109       0   
110       0   
111       0   
113       0   
114       0   
116       0   
117       0   
118       0   
120       0   
121       0   
122       0   
123       0   
124       0   
125       0   
126       0   
127       0   
129       0   
130       0   
131       0   
132       0   
133       0   
134       0   
136       0   
137       0   
138       0   
139       0   
141       0   
142       0   
143       0   
144       0   
147       0   
150       0   
151       0   
152       1   
155       0   
156       0   
159       0   
160       0   
161       0   
163       0   
165       0   
166       0   
167       0   
168       0   
169       0   
170       0   
173       0   
174       0   
175       0   
176       0   
177       0   
178       0   
180       0   
181       0   
182       0   
183       0   
184       0   
185       0   
186       0   
187       0   
188       0   
189       0   
190       0   
191       0   
193       0   
194       0   
195       0   
198       0   
200       0   
201       0   
202       0   
203       0   
204       0   
205       0   
206       0   
207       0   
208       0   
209       0   
210       0   
212       0   
213       0   
214       0   
215       0   
216       0   
217       0   
219       0   
220       0   
222       0   
223       0   
224       0   
225       0   
227       0   
228       0   
229       0   
231       0   
232       0   
234       0   
235       0   
236       0   
237       0   
238       0   
239       0   
242       0   
243       0   
244       0   
245       0   
246       0   
247       0   
248       0   
250       0   
251       0   
252       0   
253       0   
254       0   
255       0   
256       0   
257       0   
259       0   
260       0   
261       0   
262       0   
264       0   
265       0   
266       0   
267       0   
268       0   
269       0   
270       0   
271       0   
272       0   
274       0   
275       0   
276       0   
277       0   
279       0   
280       0   
281       0   
282       0   
283       0   
284       0   
285       0   
286       0   
287       0   
288       0   
289       0   
290       0   
291       0   
292       0   
293       0   
294       0   
295       0   
296       0   
297       0   
298       0   
300       0   
302       0   
303       0   
305       0   
307       0   
310       0   
311       0   
312       0   
313       0   
315       0   
316       0   
317       0   
318       0   
319       0   
320       0   
323       0   
324       0   
326       0   
329       0   
330       0   
332       0   
3

In [ ]:
# training.loc[train_indexes_list, 'ADR'] = y_pred_train
# validation.loc[valid_indexes_list, 'ADR'] = y_pred_valid

In [ ]:
# training.to_csv("training_data_with_ADR.csv")
# validation.to_csv("validation_data_with_ADR.csv")

In [ ]:
# Cross-check that it is correctly mapped
# print(f"F1-score: {f1_score(training.label, training.ADR)}\n", f"Classification report: \n{classification_report(training.label, training.ADR)}", sep='\n')

F1-score: 0.9996512033484479

Classification report: 
              precision    recall  f1-score   support

           0       1.00      1.00      1.00       739
           1       1.00      1.00      1.00      1433

    accuracy                           1.00      2172
   macro avg       1.00      1.00      1.00      2172
weighted avg       1.00      1.00      1.00      2172

